# DM project: cheese

In [43]:
import pandas as pd
from mlxtend.preprocessing import TransactionEncoder
from mlxtend.frequent_patterns import apriori
from geopy.geocoders import Nominatim
import matplotlib.pyplot as plt
import time
import tqdm.notebook as tqdm
import random


In [44]:
data=pd.read_csv("cheeses.csv")
data

cheese                                        url   milk  \
0            Aarewasser         https://www.cheese.com/aarewasser/    cow   
1      Abbaye de Belloc   https://www.cheese.com/abbaye-de-belloc/  sheep   
2      Abbaye de Belval   https://www.cheese.com/abbaye-de-belval/    cow   
3     Abbaye de Citeaux  https://www.cheese.com/abbaye-de-citeaux/    cow   
4       Abbaye de Tamié              https://www.cheese.com/tamie/    cow   
...                 ...                                        ...    ...   
1182          Sveciaost          https://www.cheese.com/sveciaost/    cow   
1183               Swag               https://www.cheese.com/swag/   goat   
1184          Swaledale          https://www.cheese.com/swaledale/  sheep   
1185  Sweet Style Swiss  https://www.cheese.com/sweet-style-swiss/    NaN   
1186       Swiss cheese              https://www.cheese.com/swiss/    cow   

            country                      region        family  \
0       Switzerland                         NaN           NaN   
1            France                 Pays Basque           NaN   
2            France                         NaN           NaN   
3            France                    Burgundy           NaN   
4            France                      Savoie           NaN   
...             ...                         ...           ...   
1182         Sweden          Low-laying regions           NaN   
1183      Australia             South Australia           NaN   
1184        England  Swaledale, North Yorkshire           NaN   
1185    Switzerland                         NaN           NaN   
1186  United States                         NaN  Swiss Cheese   

                            type fat_content calcium_content  \
0                      semi-soft         NaN             NaN   
1             semi-hard, artisan         NaN             NaN   
2                      semi-hard      40-46%             NaN   
3     semi-soft, artisan, brined         NaN             NaN   
4                  soft, artisan         NaN             NaN   
...                          ...         ...             ...   
1182           semi-hard, brined         45%             NaN   
1183         fresh firm, artisan         NaN             NaN   
1184                        hard         NaN             NaN   
1185          semi-hard, artisan         NaN             NaN   
1186    hard, artisan, processed  7.8 g/100g             NaN   

                    texture        rind        color                 flavor  \
0                   buttery      washed       yellow                  sweet   
1       creamy, dense, firm     natural       yellow          burnt caramel   
2                   elastic      washed        ivory                    NaN   
3     creamy, dense, smooth      washed        white  acidic, milky, smooth   
4      creamy, open, smooth      washed        white          fruity, nutty   
...                     ...         ...          ...                    ...   
1182         creamy, supple    rindless  pale yellow                 acidic   
1183        creamy, crumbly  ash coated        white         acidic, creamy   
1184              semi firm         NaN       yellow          smooth, sweet   
1185           firm, supple       waxed          NaN                  nutty   
1186                   firm    rindless  pale yellow           nutty, sweet   

                  aroma vegetarian  vegan                     synonyms  \
0               buttery      False  False                          NaN   
1              lanoline       True  False  Abbaye Notre-Dame de Belloc   
2              aromatic      False  False                          NaN   
3     barnyardy, earthy      False  False                          NaN   
4     perfumed, pungent      False  False                          NaN   
...                 ...        ...    ...                          ...   
1182                NaN      False  False                          NaN   
1

## Cleaning

In [45]:
print(set(data["color"]))
data[pd.isnull(data["color"])]

{'pale yellow', 'blue', 'brownish yellow', 'ivory', 'orange', 'brown', 'straw', 'blue-grey', 'cream', 'pale white', 'red', 'green', nan, 'golden yellow', 'white', 'golden orange', 'pink and white', 'yellow'}


cheese                                        url  \
10             Acapella           https://www.cheese.com/acapella/   
13                Acorn              https://www.cheese.com/acorn/   
19        Afuega'l Pitu       https://www.cheese.com/afuegal-pitu/   
48      Alpe di Frabosa    https://www.cheese.com/alpe-di-frabosa/   
50            Alpicrème          https://www.cheese.com/alpicreme/   
...                 ...                                        ...   
1172     Strathdon Blue     https://www.cheese.com/strathdon-blue/   
1175      String Cheese             https://www.cheese.com/string/   
1177            Sulguni            https://www.cheese.com/sulguni/   
1181    Sussex Slipcote    https://www.cheese.com/sussex-slipcote/   
1185  Sweet Style Swiss  https://www.cheese.com/sweet-style-swiss/   

              milk         country              region family  \
10            goat   United States          California    NaN   
13           sheep  United Kingdom            Bethania    NaN   
19             cow           Spain            Asturias    NaN   
48             cow           Italy                 NaN    NaN   
50            goat          France                 NaN    NaN   
...            ...             ...                 ...    ...   
1172           cow        Scotland                Tain   Blue   
1175           NaN             NaN                 NaN    NaN   
1177  buffalo, cow         Georgia  Svaneti, Samegrelo    NaN   
1181         sheep         England                 NaN    NaN   
1185           NaN     Switzerland                 NaN    NaN   

                    type fat_content calcium_content               texture  \
10    soft, soft-ripened         NaN             NaN                   NaN   
13         hard, artisan         52%             NaN         crumbly, firm   
19         soft, artisan         NaN             NaN                smooth   
48             semi-soft         NaN             NaN                   NaN   
50                  soft         NaN             NaN                   NaN   
...                  ...         ...             ...                   ...   
1172           semi-soft         NaN             NaN                creamy   
1175           semi-hard         NaN             NaN  chewy, firm, stringy   
1177           semi-firm         NaN             NaN        dense, elastic   
1181                soft         NaN             NaN                   NaN   
1185  semi-hard, artisan         NaN             NaN          firm, supple   

               rind color                              flavor  \
10              NaN   NaN                             buttery   
13              NaN   NaN  burnt caramel, citrusy, herbaceous   
19    cloth wrapped   NaN                       spicy, strong   
48              NaN   NaN                              bitter   
50              NaN   NaN                                 NaN   
...             ...   ...                                 ...   
1172            NaN   NaN                       creamy, spicy   
1175            NaN   NaN                                 NaN   
1177            NaN   NaN                salty, smokey , sour   
1181            NaN   NaN                               sharp   
1185          waxed   NaN                               nutty   

                aroma vegetarian  vegan                synonyms  \
10      fresh, herbal      False  False                     NaN   
13             fruity       True  False                     NaN   
19                NaN      False  False                     NaN   
48    milky, mushroom      False  False                     NaN   
50                NaN      False  False                     NaN   
...               ...        ...    ...                     ...   
1172   aromatic, rich       True  False                     NaN   
1175              NaN        NaN    NaN                     NaN   
1177              NaN        NaN    NaN  Georgian Pickle Cheese   
1181   

In [46]:
print(len(data[pd.isnull(data["calcium_content"])]))
print(len(data[pd.isnull(data["fat_content"])]))

1162
939


In [47]:
del data["alt_spellings"]
del data["producers"]
del data["calcium_content"]
del data["url"]
del data["fat_content"]
del data["synonyms"]

In [48]:
data

cheese   milk        country                      region  \
0            Aarewasser    cow    Switzerland                         NaN   
1      Abbaye de Belloc  sheep         France                 Pays Basque   
2      Abbaye de Belval    cow         France                         NaN   
3     Abbaye de Citeaux    cow         France                    Burgundy   
4       Abbaye de Tamié    cow         France                      Savoie   
...                 ...    ...            ...                         ...   
1182          Sveciaost    cow         Sweden          Low-laying regions   
1183               Swag   goat      Australia             South Australia   
1184          Swaledale  sheep        England  Swaledale, North Yorkshire   
1185  Sweet Style Swiss    NaN    Switzerland                         NaN   
1186       Swiss cheese    cow  United States                         NaN   

            family                        type                texture  \
0              NaN                   semi-soft                buttery   
1              NaN          semi-hard, artisan    creamy, dense, firm   
2              NaN                   semi-hard                elastic   
3              NaN  semi-soft, artisan, brined  creamy, dense, smooth   
4              NaN               soft, artisan   creamy, open, smooth   
...            ...                         ...                    ...   
1182           NaN           semi-hard, brined         creamy, supple   
1183           NaN         fresh firm, artisan        creamy, crumbly   
1184           NaN                        hard              semi firm   
1185           NaN          semi-hard, artisan           firm, supple   
1186  Swiss Cheese    hard, artisan, processed                   firm   

            rind        color                 flavor              aroma  \
0         washed       yellow                  sweet            buttery   
1        natural       yellow          burnt caramel           lanoline   
2         washed        ivory                    NaN           aromatic   
3         washed        white  acidic, milky, smooth  barnyardy, earthy   
4         washed        white          fruity, nutty  perfumed, pungent   
...          ...          ...                    ...                ...   
1182    rindless  pale yellow                 acidic                NaN   
1183  ash coated        white         acidic, creamy              fresh   
1184         NaN       yellow          smooth, sweet             floral   
1185       waxed          NaN                  nutty       nutty, sweet   
1186    rindless  pale yellow           nutty, sweet                NaN   

     vegetarian  vegan  
0         False  False  
1          True  False  
2         False  False  
3         False  False  
4         False  False  
...         ...    ...  
1182      False  False  
1183       True  False  
1184       True  False  
1185      False  False  
1186       True  False  

[1187 rows x 13 columns]

In [49]:
data=data.dropna(subset=["country","region"], how="all")
data["country"]=data["country"].fillna("")
data["region"]=data["region"].fillna("")
print(f"{len(data)} rows remaining")

1181 rows remaining


/tmp/ipykernel_13743/3522053431.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["country"]=data["country"].fillna("")
/tmp/ipykernel_13743/3522053431.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["region"]=data["region"].fillna("")


We removed 6 rows for which we could not find a suitable location. 

In [50]:
data.loc[data.country.str.contains("England, Great Britain, United Kingdom")|data.country.str.contains("England, United Kingdom"),"country"]="England"
data.loc[data.country.str.contains("Scotland"),"country"]="Scotland"
data.loc[data.country.str.contains("Great Britain, United Kingdom, Wales")|data.country.str.contains("United Kingdom, Wales"),"country"]="Wales"


In [51]:
print(len(data[data["country"].str.contains(",")]))
data[data["country"].str.contains(",")]


39


cheese                milk  \
12                              Ackawi    cow, goat, sheep   
116                             Baladi    cow, goat, sheep   
160                   Beemster 2% Milk                 cow   
212                    Blissful Blocks                 NaN   
213                  Blissful Toppings                 NaN   
243                         Bootlegger          cow, sheep   
262                     Brebis d'Azure               sheep   
297                            Brunost           cow, goat   
300                            Bryndza               sheep   
311                            Burrata       water buffalo   
316                         Butterkase                 cow   
367                         Cap Cressy                goat   
375                          Capri Blu                goat   
377                            Caprice                goat   
407                         Casu marzu               sheep   
437                       Cheese Curds                 NaN   
445                            Chhurpi            cow, yak   
455                        Chura Kampo                 yak   
508                     Cottage Cheese                 cow   
512        Counting Sheep…and Goats...    cow, goat, sheep   
524                 Cream Cheesy Bliss                 NaN   
537                         Cressy Blu                 cow   
569      La Couronne - Fort Aged Comté                 cow   
601                       Lamb Chopper               sheep   
621   Le Conquerant Demi Pont L'eveque                 cow   
646                          Limburger                 cow   
675                            Lunetta                 cow   
701                          Mamirolle                 cow   
776                  Monastery Cheeses                 cow   
789                      Monterey Jack                 cow   
852                             Paneer  cow, water buffalo   
975            President Fat Free Feta                 cow   
1001                   Purple's a Must           cow, goat   
1082                         Shanklish          cow, sheep   
1099                    Shredded Bliss                 NaN   
1106                            Sirene    cow, goat, sheep   
1108                   Slices Of Bliss                 NaN   
1123                             Sosha           goat, yak   
1173                   Strawberry Moon                 cow   

                                                country  \
12    Cyprus, Egypt, Israel, Jordan, Lebanon, Middle...   
116                                Lebanon, Middle East   
160   Canada, Denmark, France, Germany, Netherlands,...   
212                               Canada, United States   
213                               Canada, United States   
243                                       Canada, Italy   
262                                       Canada, Italy   
297   Denmark, Finland, Germany, Iceland, Norway, Sw...   
300                           Hungary, Poland, Slovakia   
311                                Italy, United States   
316                                    Austria, Germany   
367                                       Canada, Italy   
375                                       Canada, Italy   
377                                       Canada, Italy   
407                                       France, Italy   
437                        Canada, India, United States   
445                                 China, Nepal, Tibet   
455                                        China, Tibet   
508                       United Kingdom, United States   
512                                       Canada, Italy   
524                               Canada, United States   
537                                       Canada, Italy   
569                                 France, Switzerland   
601                          Netherlands, United States   
621                                   Australia, France   
646              

In [52]:
data=data.drop(index=data[data["country"].str.contains(",")].index)

We removed 39 cheeses because they can come froms several countries. 

In [53]:
data["location"]=data["region"]+", "+data["country"]

In [54]:
data

cheese   milk        country                      region  \
0            Aarewasser    cow    Switzerland                               
1      Abbaye de Belloc  sheep         France                 Pays Basque   
2      Abbaye de Belval    cow         France                               
3     Abbaye de Citeaux    cow         France                    Burgundy   
4       Abbaye de Tamié    cow         France                      Savoie   
...                 ...    ...            ...                         ...   
1182          Sveciaost    cow         Sweden          Low-laying regions   
1183               Swag   goat      Australia             South Australia   
1184          Swaledale  sheep        England  Swaledale, North Yorkshire   
1185  Sweet Style Swiss    NaN    Switzerland                               
1186       Swiss cheese    cow  United States                               

            family                        type                texture  \
0              NaN                   semi-soft                buttery   
1              NaN          semi-hard, artisan    creamy, dense, firm   
2              NaN                   semi-hard                elastic   
3              NaN  semi-soft, artisan, brined  creamy, dense, smooth   
4              NaN               soft, artisan   creamy, open, smooth   
...            ...                         ...                    ...   
1182           NaN           semi-hard, brined         creamy, supple   
1183           NaN         fresh firm, artisan        creamy, crumbly   
1184           NaN                        hard              semi firm   
1185           NaN          semi-hard, artisan           firm, supple   
1186  Swiss Cheese    hard, artisan, processed                   firm   

            rind        color                 flavor              aroma  \
0         washed       yellow                  sweet            buttery   
1        natural       yellow          burnt caramel           lanoline   
2         washed        ivory                    NaN           aromatic   
3         washed        white  acidic, milky, smooth  barnyardy, earthy   
4         washed        white          fruity, nutty  perfumed, pungent   
...          ...          ...                    ...                ...   
1182    rindless  pale yellow                 acidic                NaN   
1183  ash coated        white         acidic, creamy              fresh   
1184         NaN       yellow          smooth, sweet             floral   
1185       waxed          NaN                  nutty       nutty, sweet   
1186    rindless  pale yellow           nutty, sweet                NaN   

     vegetarian  vegan                             location  
0         False  False                        , Switzerland  
1          True  False                  Pays Basque, France  
2         False  False                             , France  
3         False  False                     Burgundy, France  
4         False  False                       Savoie, France  
...         ...    ...                                  ...  
1182      False  False           Low-laying regions, Sweden  
1183       True  False           South Australia, Australia  
1184       True  False  Swaledale, North Yorkshire, England  
1185      False  False                        , Switzerland  
1186       True  False                      , United States  

[1142 rows x 14 columns]

In [55]:
locs=set(data["location"])
locs

{', Afghanistan',
 ', Argentina',
 ', Armenia',
 ', Australia',
 ', Austria',
 ', Belgium',
 ', Brazil',
 ', Canada',
 ', Cyprus',
 ', Denmark',
 ', England',
 ', France',
 ', Germany',
 ', Greece',
 ', Holland',
 ', Hungary',
 ', Iceland',
 ', Iraq',
 ', Ireland',
 ', Israel',
 ', Italy',
 ', Mauritania',
 ', Mexico',
 ', Mexico and Caribbean',
 ', Middle East',
 ', Mongolia',
 ', Netherlands',
 ', New Zealand',
 ', Poland',
 ', Portugal',
 ', Scotland',
 ', Serbia',
 ', Spain',
 ', Sweden',
 ', Switzerland',
 ', Turkey',
 ', United Kingdom',
 ', United States',
 ', Wales',
 'Aberdeenshire, Scotland',
 'Aconcagua, Chile',
 'Adamstown, Co Wexford, Ireland',
 'Airedale farming district, New Zealand',
 'Alba, Italy',
 'All Holland, Netherlands',
 'Allagau, Bavarian Alps, Germany',
 'Allgaeu Alps, Germany',
 'Allgau, Germany',
 'Allgäu, Germany',
 'Amou, Gascony, France',
 'Anjou, France',
 'Ann Arbor, MI, United States',
 'Ann Arbor, Michigan, United States',
 'Aquitaine, France',
 'Asia

In [69]:
def str_to_gps(loc):
    l=loc.split(",")
    loc=",".join([l[0],l[-1]])# removing details gives less errors while fetching the GPS coordinates
    try:
        res=Nominatim(user_agent="dmProject").geocode(loc) 
        return (res.latitude, res.longitude)
    except AttributeError:
        loc=l[-1]
        res=Nominatim(user_agent="dmProject").geocode(loc) 
        return (res.latitude, res.longitude)

In [70]:
locations_to_gps={}
errors=set()
for loc in tqdm.tqdm(locs):
    time.sleep(1)
    try:
        locations_to_gps[loc]=str_to_gps(loc)
        print(loc, locations_to_gps[loc])
    except AttributeError:
        print(loc, "ERROR")
        errors.add(loc)

  0%|          | 0/390 [00:00<?, ?it/s]

Valencia, Spain (39.4697065, -0.3763353)
Crotone, Italy (39.1873894, 16.87828188895307)
New Hampshire, United States (43.4849133, -71.6553992)
Setubal, Palmela and Sesimbra, Portugal (38.5241783, -8.8932341)
, Turkey (39.294076, 35.2316631)
Wisconsin, United States (44.4308975, -89.6884637)
Maine, United States (45.709097, -68.8590201)
Beara Peninsula, Co. Cork, Ireland (51.7280451, -9.767906428362338)
Castilla Leon, Spain (40.4598868, -3.4720773)
, Wales (52.2928116, -3.73893)
Romanian Carpathians, Romania (46.4046483, 22.9894841933513)
Pembrokeshire, Wales (51.8339209, -4.916667)
Lodi, Italy (45.2613104, 9.491678060021837)
Stoneyford, Ireland (52.5362671, -7.2278963)
Central and Western Macedonia, Thessaly, Greece (38.9953683, 21.9877132)
, Armenia (4.536307, -75.6723751)
Indiana, United States (40.3270127, -86.1746933)
Alba, Italy (44.7007236, 8.0357786)
East Sussex, United Kingdom (50.9404266, 0.3699977891068864)
Fornells de la Selva, Gironès, Spain (41.9319675, 2.8090343)
, Iraq (

In [71]:
print(locations_to_gps)

{'Valencia, Spain': (39.4697065, -0.3763353), 'Crotone, Italy': (39.1873894, 16.87828188895307), 'New Hampshire, United States': (43.4849133, -71.6553992), 'Setubal, Palmela and Sesimbra, Portugal': (38.5241783, -8.8932341), ', Turkey': (39.294076, 35.2316631), 'Wisconsin, United States': (44.4308975, -89.6884637), 'Maine, United States': (45.709097, -68.8590201), 'Beara Peninsula, Co. Cork, Ireland': (51.7280451, -9.767906428362338), 'Castilla Leon, Spain': (40.4598868, -3.4720773), ', Wales': (52.2928116, -3.73893), 'Romanian Carpathians, Romania': (46.4046483, 22.9894841933513), 'Pembrokeshire, Wales': (51.8339209, -4.916667), 'Lodi, Italy': (45.2613104, 9.491678060021837), 'Stoneyford, Ireland': (52.5362671, -7.2278963), 'Central and Western Macedonia, Thessaly, Greece': (38.9953683, 21.9877132), ', Armenia': (4.536307, -75.6723751), 'Indiana, United States': (40.3270127, -86.1746933), 'Alba, Italy': (44.7007236, 8.0357786), 'East Sussex, United Kingdom': (50.9404266, 0.36999778910

In [75]:
print(errors)

{', Mexico and Caribbean'}


In [76]:
len(errors)

1

In [ ]:
len(locations)
locations
x=[]
y=[]
for l in locations:
    if l is not None:
        x.append(l[0])
        y.append(l[1])
plt.plot(x,y,".")

In [ ]:
def filter_df(df, cols=None):
    if cols is None:
        cols = ["milk", "country", "type", "texture", "flavor", "aroma", "family", "rind"]

    df = df.copy()
    attributes = set() # Get all the possible attributes (some are mixed in different columns)
    for col in cols:
        values = set()
        for val in set(df[col]):
            if type(val) == float: # skip NaN values
                continue
            values = values.union([x.strip() for x in set(val.split(","))])
        attributes = attributes.union(values)
    
    
    row_attrs = [set() for _ in range(len(df))] # get the attributes specific to each row
    for col in cols:
        for i, row in enumerate(df[col]):
            if type(row) != float:
                row_attrs[i] = row_attrs[i].union([x.strip() for x in row.split(",")])

    for attr in attributes: # Add attributes rows
        df[attr] = list(attr in row_attrs[i] for i in range(len(df[col])))
    for col in cols:
        del df[col]

    return df.copy()

In [ ]:
data_features=filter_df(data)

## Classification

In [ ]:
from sklearn import tree

In [ ]:
c=tree.DecisionTreeClassifier()

In [ ]:
c.fit(

In [ ]:
data[["country","region"]]

Transformer:  la couleur en RGB; la localisation en GPS
1ère question: est-ce que la couleur suffit à savoir d'où ça vient ? 
2ème question: est-ce que si on ajoute le type ça marche ? 
3ème question: et les caractéristiques gustatives ?


In [ ]:
data_features

In [ ]:
data[pd.isnull(data["country"])&pd.isnull(data["region"])]


## Pattern Mining

In [ ]:
data

In [ ]:
apriori(data)